# Attempt to forecast the price of MSFT by analyzing the prices of multiple stocks, including MSFT, over several consecutive days leading up to the target day.
#### N.B. Different setup from HW1

In [1]:
from torch.utils.data import DataLoader,Dataset

class StockDataset(Dataset):
    def __init__(self,X,Y,days):
        self.X = X
        self.Y = Y.reshape(-1)
        self.days = days # days ahead for prediction

    def __len__(self):
        return (len(self.Y)-self.days)

    def __getitem__(self,index):
        x=self.X[:,index:index+self.days]
        y=self.Y[index+self.days]
        return x,y



In [2]:
# !pip install pandas
# !pip install yfinance
import numpy as np
from numpy import exp, sum, log, log10
import yfinance as yf
import pandas as pd

def get_price(tick,start='2020-01-01',end=None):
    return yf.Ticker(tick).history(start=start,end=end)['Close']

def get_prices(tickers,start='2020-01-01',end=None):
    df=pd.DataFrame()
    for s in tickers:
        df[s]=get_price(s,start,end)
    return df

feature_stocks=['tsla','meta','nvda','amzn','nflx','gbtc','gdx','intc','dal','c','goog','aapl','msft','ibm','hp','orcl','sap','crm','hubs','twlo']
predict_stock='msft'

# getting data
start_date='2020-01-01'

allX=get_prices(feature_stocks,start=start_date)
ally=get_prices([predict_stock],start=start_date)

In [3]:
import torch.utils.data as data
import torch

stockData = StockDataset(allX.to_numpy().transpose().astype(np.float32),ally.to_numpy().astype(np.float32),days=5)
train_set_size = int(len(stockData)*0.7)
valid_set_size = int(len(stockData)*0.2)
test_set_size = len(stockData)-train_set_size-valid_set_size

train_set, valid_set, test_set = data.random_split(stockData,[train_set_size,valid_set_size,test_set_size],\
                                              generator=torch.Generator().manual_seed(42))

batch_size = train_set_size # use entire dataset as batch
train_dataloader = DataLoader(train_set,batch_size=batch_size,shuffle=True)  # input:(20,5), label:1
valid_dataloader = DataLoader(valid_set,batch_size=batch_size,shuffle=False)
test_dataloader = DataLoader(test_set,batch_size=batch_size,shuffle=False)

# 1. Build a simple MLP to forecast MSFT price using PyTorch Lightning.

#### You have total freedom of your MLP. But your MLP should take the last five day ($5 \times 20=100$) prices as input and you have to add dropout into your network.

## 1a. Create a subclass of pytorch_lightning.LightningModule. It should include \_\_init\_\_, training_step, validation_step, configure_optimizers in the class. (6 points)

In [7]:
!pip install pytorch-lightning
import torch.nn as nn
import pytorch_lightning as pl
import torch


class StockPriceMLP(pl.LightningModule):
    def __init__(self, input_dim=100, hidden_dim=128, dropout_rate=0.3, lr=1e-3):
        super().__init__()
        self.save_hyperparameters()

        self.model = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Linear(hidden_dim, hidden_dim),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Linear(hidden_dim, 1)
        )

        self.loss_fn = nn.MSELoss()

    def forward(self, x):
        return self.model(x).squeeze()

    def training_step(self, batch, batch_idx):
        x, y = batch
        x = x.view(x.size(0), -1)  # Flatten (batch_size, 5×20)
        y_hat = self(x)
        loss = self.loss_fn(y_hat, y)
        self.log('train_mse', loss)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        x = x.view(x.size(0), -1)
        y_hat = self(x)
        loss = self.loss_fn(y_hat, y)
        self.log('val_mse', loss, prog_bar=True)
        return loss

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=self.hparams.lr)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.0/823.0 kB 12.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 95.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 77.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 47.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 3.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 64.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 960.9/960.9 kB 47.1 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-

## 1b. Create a subclass of pytorch_lightning.LightningDataModule. It should include \_\_init\_\_, train_dataloader, and val_dataloader in the class. (4 points)

In [8]:
class StockDataModule(pl.LightningDataModule):
    def __init__(self, dataset, batch_size):
        super().__init__()
        self.dataset = dataset
        self.batch_size = batch_size

    def setup(self, stage=None):
        dataset_size = len(self.dataset)
        train_size = int(dataset_size * 0.7)
        val_size = int(dataset_size * 0.15)
        test_size = dataset_size - train_size - val_size

        self.train_set, self.val_set, self.test_set = torch.utils.data.random_split(
            self.dataset, [train_size, val_size, test_size],
            generator=torch.Generator().manual_seed(42)
        )

    def train_dataloader(self):
        return DataLoader(self.train_set, batch_size=self.batch_size, shuffle=True)

    def val_dataloader(self):
        return DataLoader(self.val_set, batch_size=self.batch_size)

    def test_dataloader(self):
        return DataLoader(self.test_set, batch_size=self.batch_size)


## 1c. Complete the rest of the code and train the model with 70% of the data. You should set aside 15% of the data each for validation and testing.  Show the training and validation MSE (5 points)

In [9]:
import pytorch_lightning as pl

# Instantiate DataModule
stock_dm = StockDataModule(stockData, batch_size=len(stockData))

# Initialize model
model = StockPriceMLP()

# Create Trainer
trainer = pl.Trainer(
    max_epochs=100,
    enable_checkpointing=False,
    enable_progress_bar=True,
    logger=False
)

# Train the model
trainer.fit(model, datamodule=stock_dm)


INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type       | Params | Mode 
-----------------------------------------------
0 | model   | Sequential | 29.6 K | train
1 | loss_fn | MSELoss    | 0      | train
-----------------------------------------------
29.6 K    Trainable params
0         Non-trainable params
29.6 K    Total params
0.118     Total estimated model params size (MB)
9         Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.


# 2. Construct a 1-D CNN to forecast MSFT stock price. You are free to use any design, but your network must consist of at least one convolutional layer and one dropout layer. You can also extend the duration leading up to the target day by modifying the "days" argument in the StockDataset. But "days" should not be larger than 32. (10 points)


In [15]:
# Step 1: Set number of days to 25
days = 25
stockData = StockDataset(allX.to_numpy().transpose().astype(np.float32),
                         ally.to_numpy().astype(np.float32),
                         days=days)


In [16]:
import pytorch_lightning as pl
import torch.nn as nn
import torch

class StockPriceCNN(pl.LightningModule):
    def __init__(self, num_stocks=20, days=25, dropout_rate=0.3, lr=1e-3):
        super().__init__()
        self.save_hyperparameters()
        self.train_losses = []
        self.val_losses = []

        self.cnn = nn.Sequential(
            nn.Conv1d(in_channels=num_stocks, out_channels=64, kernel_size=3, padding=1),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Conv1d(64, 32, kernel_size=3, padding=1),
            nn.ReLU(),
            nn.Flatten(),
            nn.Linear(32 * days, 128),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Linear(128, 1)
        )
        self.loss_fn = nn.MSELoss()

    def forward(self, x):
        return self.cnn(x).squeeze()

    def training_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self(x)
        loss = self.loss_fn(y_hat, y)
        self.train_losses.append(loss.item())
        self.log('train_mse', loss)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self(x)
        loss = self.loss_fn(y_hat, y)
        self.val_losses.append(loss.item())
        self.log('val_mse', loss, prog_bar=True)
        return loss

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=self.hparams.lr)


In [17]:
from torch.utils.data import DataLoader

class StockDataModule(pl.LightningDataModule):
    def __init__(self, dataset, batch_size):
        super().__init__()
        self.dataset = dataset
        self.batch_size = batch_size

    def setup(self, stage=None):
        dataset_size = len(self.dataset)
        train_size = int(dataset_size * 0.7)
        val_size = int(dataset_size * 0.15)
        test_size = dataset_size - train_size - val_size

        self.train_set, self.val_set, self.test_set = torch.utils.data.random_split(
            self.dataset, [train_size, val_size, test_size],
            generator=torch.Generator().manual_seed(42)
        )

    def train_dataloader(self):
        return DataLoader(self.train_set, batch_size=self.batch_size, shuffle=True)

    def val_dataloader(self):
        return DataLoader(self.val_set, batch_size=self.batch_size)

    def test_dataloader(self):
        return DataLoader(self.test_set, batch_size=self.batch_size)


In [18]:
stock_dm = StockDataModule(stockData, batch_size=len(stockData))
cnn_model = StockPriceCNN(num_stocks=20, days=25)

trainer = pl.Trainer(
    max_epochs=100,
    enable_checkpointing=False,
    logger=False,
    enable_progress_bar=True
)

trainer.fit(cnn_model, datamodule=stock_dm)



INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type       | Params | Mode 
-----------------------------------------------
0 | cnn     | Sequential | 112 K  | train
1 | loss_fn | MSELoss    | 0      | train
-----------------------------------------------
112 K     Trainable params
0         Non-trainable params
112 K     Total params
0.451     Total estimated model params size (MB)
12        Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.


In [19]:
test_loader = stock_dm.test_dataloader()
cnn_model.eval()

with torch.no_grad():
    for x, y in test_loader:
        y_pred = cnn_model(x)
        test_mse = nn.MSELoss()(y_pred, y)
        print(f"Test MSE: {test_mse.item():.4f}")


Test MSE: 1554.7102


In [20]:
import pandas as pd

print(f"\nFinal Training MSE: {cnn_model.train_losses[-1]:.6f}")
print(f"Final Validation MSE: {cnn_model.val_losses[-1]:.6f}")

train_size = len(stock_dm.train_set)
val_size = len(stock_dm.val_set)
test_size = len(stock_dm.test_set)

split_table = pd.DataFrame({
    "Split": ["Train", "Validation", "Test"],
    "Size": [train_size, val_size, test_size]
})

print("\nDataset Split Summary:")
print(split_table.to_string(index=False))



Final Training MSE: 1138.270996
Final Validation MSE: 1542.800537

Dataset Split Summary:
     Split  Size
     Train   904
Validation   193
      Test   195


# 3. Please try to enhance the performance of the previously created MLP or CNN by applying hyperparameter tuning. You can use tools such as W&B hyperparameter sweep, SMAP, Optuna, or similar packages to achieve this. You need to optimize at least two parameters, with the dropout rate being one of them. (5 points)












In [21]:
!pip install optuna


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 383.6/383.6 kB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 17.9 MB/s eta 0:00:00


In [22]:
import optuna
import torch
import torch.nn as nn
import pytorch_lightning as pl
from pytorch_lightning import Trainer
from torch.utils.data import DataLoader

def objective(trial):

    # Hyperparameters to tune
    dropout_rate = trial.suggest_float("dropout_rate", 0.1, 0.5)
    lr = trial.suggest_loguniform("lr", 1e-5, 1e-2)

    class TunedStockPriceCNN(pl.LightningModule):
        def __init__(self, num_stocks=20, days=25):
            super().__init__()
            self.save_hyperparameters()
            self.cnn = nn.Sequential(
                nn.Conv1d(in_channels=num_stocks, out_channels=64, kernel_size=3, padding=1),
                nn.ReLU(),
                nn.Dropout(dropout_rate),
                nn.Conv1d(64, 32, kernel_size=3, padding=1),
                nn.ReLU(),
                nn.Flatten(),
                nn.Linear(32 * days, 128),
                nn.ReLU(),
                nn.Dropout(dropout_rate),
                nn.Linear(128, 1)
            )
            self.loss_fn = nn.MSELoss()

        def forward(self, x):
            return self.cnn(x).squeeze()

        def training_step(self, batch, batch_idx):
            x, y = batch
            y_hat = self(x)
            loss = self.loss_fn(y_hat, y)
            return loss

        def validation_step(self, batch, batch_idx):
            x, y = batch
            y_hat = self(x)
            loss = self.loss_fn(y_hat, y)
            self.log("val_mse", loss, prog_bar=True)
            return loss

        def configure_optimizers(self):
            return torch.optim.Adam(self.parameters(), lr=lr)

    # Use previously defined datamodule
    model = TunedStockPriceCNN()
    trainer = Trainer(
        max_epochs=30,
        enable_checkpointing=False,
        logger=False,
        enable_progress_bar=False
    )

    trainer.fit(model, datamodule=stock_dm)

    val_mse = trainer.callback_metrics["val_mse"].item()
    return val_mse


In [23]:
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=20)

# Best hyperparameters
print("\nBest Hyperparameters:")
print(study.best_params)

# Best validation MSE
print(f"Best Validation MSE: {study.best_value:.4f}")


[I 2025-03-30 19:30:15,829] A new study created in memory with name: no-name-2d391d70-c156-445b-93aa-3f6e5ee246c2
<ipython-input-22-556288d7dc2b>:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr = trial.suggest_loguniform("lr", 1e-5, 1e-2)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type       | Params | Mode 
-----------------------------------------------
0 | cnn     | Sequential | 112 K  | train
1 | loss_fn | MSELoss    | 0      | train
-----------------------------------------------
112 K     Trainable params
0         Non-trainable params
112 K     Total params
0.45


Best Hyperparameters:
{'dropout_rate': 0.23788169893393854, 'lr': 0.0010732053716142177}
Best Validation MSE: 1257.5607


In [24]:
best_dropout = study.best_params["dropout_rate"]
best_lr = study.best_params["lr"]

# Final tuned model
final_model = StockPriceCNN(num_stocks=20, days=25, dropout_rate=best_dropout, lr=best_lr)

# Train final model
trainer = Trainer(max_epochs=100, logger=False, enable_progress_bar=True)
trainer.fit(final_model, datamodule=stock_dm)


INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type       | Params | Mode 
-----------------------------------------------
0 | cnn     | Sequential | 112 K  | train
1 | loss_fn | MSELoss    | 0      | train
-----------------------------------------------
112 K     Trainable params
0         Non-trainable params
112 K     Total params
0.451     Total estimated model params size (MB)
12        Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.


In [25]:
# -------------------- Imports --------------------
import numpy as np
import pandas as pd
import yfinance as yf
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader, random_split
import pytorch_lightning as pl
from pytorch_lightning import Trainer
import optuna

# -------------------- Step 1: Data Fetching --------------------
def get_price(tick, start='2020-01-01', end=None):
    return yf.Ticker(tick).history(start=start, end=end)['Close']

def get_prices(tickers, start='2020-01-01', end=None):
    df = pd.DataFrame()
    for s in tickers:
        df[s] = get_price(s, start, end)
    return df

feature_stocks = ['tsla','meta','nvda','amzn','nflx','gbtc','gdx','intc','dal','c',
                  'goog','aapl','msft','ibm','hp','orcl','sap','crm','hubs','twlo']
predict_stock = 'msft'

allX = get_prices(feature_stocks, start='2020-01-01')
ally = get_prices([predict_stock], start='2020-01-01')

# -------------------- Step 2: Dataset --------------------
DAYS = 25

class StockDataset(Dataset):
    def __init__(self, X, Y, days):
        self.X = X
        self.Y = Y.reshape(-1)
        self.days = days

    def __len__(self):
        return len(self.Y) - self.days

    def __getitem__(self, index):
        x = self.X[:, index:index + self.days]
        y = self.Y[index + self.days]
        return x, y

dataset = StockDataset(allX.to_numpy().T.astype(np.float32),
                       ally.to_numpy().astype(np.float32),
                       days=DAYS)

# -------------------- Step 3: DataModule --------------------
class StockDataModule(pl.LightningDataModule):
    def __init__(self, dataset, batch_size):
        super().__init__()
        self.dataset = dataset
        self.batch_size = batch_size

    def setup(self, stage=None):
        total = len(self.dataset)
        train_size = int(0.7 * total)
        val_size = int(0.15 * total)
        test_size = total - train_size - val_size
        self.train_set, self.val_set, self.test_set = random_split(
            self.dataset, [train_size, val_size, test_size],
            generator=torch.Generator().manual_seed(42)
        )

    def train_dataloader(self):
        return DataLoader(self.train_set, batch_size=self.batch_size, shuffle=True)

    def val_dataloader(self):
        return DataLoader(self.val_set, batch_size=self.batch_size)

# -------------------- Step 4: CNN Model --------------------
class CNNForecast(pl.LightningModule):
    def __init__(self, dropout_rate=0.3, learning_rate=1e-3):
        super().__init__()
        self.save_hyperparameters()

        self.conv1 = nn.Conv1d(in_channels=20, out_channels=64, kernel_size=3)
        self.conv2 = nn.Conv1d(64, 32, kernel_size=3)
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(self.hparams.dropout_rate)

        conv_output_size = (DAYS - 2 - 2) * 32  # Adjusted for 2 conv layers with kernel=3
        self.fc1 = nn.Linear(conv_output_size, 64)
        self.fc2 = nn.Linear(64, 1)
        self.criterion = nn.MSELoss()

    def forward(self, x):
        x = self.conv1(x)
        x = self.relu(x)
        x = self.conv2(x)
        x = self.relu(x)
        x = self.dropout(x)
        x = x.view(x.size(0), -1)
        x = self.fc1(x)
        x = self.relu(x)
        x = self.dropout(x)
        return self.fc2(x).squeeze()

    def training_step(self, batch, batch_idx):
        x, y = batch
        x = x.permute(0, 1, 2)
        preds = self(x)
        loss = self.criterion(preds, y)
        self.log("train_mse", loss)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        x = x.permute(0, 1, 2)
        preds = self(x)
        loss = self.criterion(preds, y)
        self.log("val_mse", loss)
        return loss

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=self.hparams.learning_rate)

# -------------------- Step 5: Optuna Objective --------------------
def objective(trial):
    dropout_rate = trial.suggest_float("dropout_rate", 0.05, 0.4)
    learning_rate = trial.suggest_loguniform("learning_rate", 1e-4, 5e-3)
    batch_size = trial.suggest_categorical("batch_size", [32, 64])

    model = CNNForecast(dropout_rate=dropout_rate, learning_rate=learning_rate)
    dm = StockDataModule(dataset, batch_size=batch_size)

    trainer = Trainer(
        max_epochs=30,
        logger=False,
        enable_checkpointing=False,
        enable_progress_bar=False
    )

    trainer.fit(model, datamodule=dm)
    val_result = trainer.validate(model, datamodule=dm, verbose=False)
    return val_result[0]["val_mse"]

# -------------------- Step 6: Run the Study --------------------
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=25)

# -------------------- Step 7: Final Results --------------------
print("\nBest hyperparameters:")
print(study.best_params)
print(f"Best Validation MSE: {study.best_value:.6f}")


[I 2025-03-30 19:45:30,876] A new study created in memory with name: no-name-23d4d32b-63bf-4fde-929e-04d4ae107003
<ipython-input-25-fc2cd0d639ed>:123: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform("learning_rate", 1e-4, 5e-3)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name      | Type    | Params | Mode 
----------------------------------------------
0 | conv1     | Conv1d  | 3.9 K  | train
1 | conv2     | Conv1d  | 6.2 K  | train
2 | relu      | ReLU    | 0      | train
3 | dropout   | Dropout | 0      | train
4 | fc1       | Linear  | 43.1 K


Best hyperparameters:
{'dropout_rate': 0.11017019014252888, 'learning_rate': 0.0021647422353382097, 'batch_size': 32}
Best Validation MSE: 108.977493


Extra credit

In [29]:
# -------------------- Step 1: Imports --------------------
import numpy as np
import pandas as pd
import yfinance as yf
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader, random_split
import pytorch_lightning as pl
import os

# -------------------- Step 2: Download and Normalize Data --------------------
def get_price(tick, start='2020-01-01', end=None):
    return yf.Ticker(tick).history(start=start, end=end)['Close']

def get_prices(tickers, start='2020-01-01', end=None):
    df = pd.DataFrame()
    for s in tickers:
        df[s] = get_price(s, start, end)
    return df

feature_stocks = ['tsla','meta','nvda','amzn','nflx','gbtc','gdx','intc','dal','c',
                  'goog','aapl','msft','ibm','hp','orcl','sap','crm','hubs','twlo']
predict_stock = 'msft'

allX = get_prices(feature_stocks, start='2020-01-01')
ally = get_prices([predict_stock], start='2020-01-01')

# Normalize input features
allX = (allX - allX.mean()) / allX.std()

# Normalize target
target_mean = ally.mean().values[0]
target_std = ally.std().values[0]
ally_norm = (ally - target_mean) / target_std

y_mean = torch.tensor(target_mean, dtype=torch.float32)
y_std = torch.tensor(target_std, dtype=torch.float32)

# -------------------- Step 3: Dataset --------------------
DAYS = 25  # << Set to 25 as per your request

class StockDataset(Dataset):
    def __init__(self, X, Y, days):
        self.X = X
        self.Y = Y.reshape(-1)
        self.days = days

    def __len__(self):
        return len(self.Y) - self.days

    def __getitem__(self, index):
        x = self.X[:, index:index+self.days]
        y = self.Y[index + self.days]
        return x, y

dataset = StockDataset(allX.to_numpy().T.astype(np.float32),
                       ally_norm.to_numpy().astype(np.float32),
                       days=DAYS)

# -------------------- Step 4: DataModule --------------------
class StockDataModule(pl.LightningDataModule):
    def __init__(self, dataset, batch_size):
        super().__init__()
        self.dataset = dataset
        self.batch_size = batch_size

    def setup(self, stage=None):
        total = len(self.dataset)
        train_size = int(0.7 * total)
        val_size = int(0.15 * total)
        test_size = total - train_size - val_size
        self.train_set, self.val_set, self.test_set = random_split(
            self.dataset, [train_size, val_size, test_size],
            generator=torch.Generator().manual_seed(42)
        )

    def train_dataloader(self):
        return DataLoader(self.train_set, batch_size=self.batch_size, shuffle=True)

    def val_dataloader(self):
        return DataLoader(self.val_set, batch_size=self.batch_size)

    def test_dataloader(self):  # ✅ This was missing before
        return DataLoader(self.test_set, batch_size=self.batch_size)

# -------------------- Step 5: Final CNN Model --------------------
class FinalCNN(pl.LightningModule):
    def __init__(self, dropout_rate=0.1, learning_rate=1e-4):
        super().__init__()
        self.save_hyperparameters()

        self.conv1 = nn.Conv1d(20, 32, kernel_size=5, padding=2)
        self.bn1 = nn.BatchNorm1d(32)
        self.conv2 = nn.Conv1d(32, 64, kernel_size=3, padding=1)
        self.bn2 = nn.BatchNorm1d(64)
        self.conv3 = nn.Conv1d(64, 32, kernel_size=1)
        self.bn3 = nn.BatchNorm1d(32)
        self.residual = nn.Conv1d(32, 32, kernel_size=1)

        self.dropout = nn.Dropout(self.hparams.dropout_rate)
        self.gap = nn.AdaptiveAvgPool1d(1)
        self.fc = nn.Linear(32, 1)

        self.criterion = nn.MSELoss()

    def forward(self, x):
        x = x.permute(0, 1, 2)
        x1 = torch.nn.functional.gelu(self.bn1(self.conv1(x)))
        x2 = torch.nn.functional.gelu(self.bn2(self.conv2(x1)))
        x3 = torch.nn.functional.gelu(self.bn3(self.conv3(x2)))
        x_res = self.residual(x1) + x3
        x = self.dropout(x_res)
        x = self.gap(x).squeeze(-1)
        return self.fc(x).squeeze()

    def training_step(self, batch, batch_idx):
        x, y = batch
        loss = self.criterion(self(x), y)
        self.log("train_mse", loss)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        loss = self.criterion(self(x), y)
        self.log("val_mse", loss)
        return loss

    def test_step(self, batch, batch_idx):
        x, y = batch
        preds = self(x)
        preds_real = preds * y_std + y_mean
        y_real = y * y_std + y_mean
        loss = nn.MSELoss()(preds_real, y_real)
        self.log("test_mse", loss)
        return loss

    def configure_optimizers(self):
        optimizer = torch.optim.AdamW(self.parameters(), lr=self.hparams.learning_rate, weight_decay=1e-4)
        scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=50, gamma=0.7)
        return {"optimizer": optimizer, "lr_scheduler": scheduler}

# -------------------- Step 6: Train & Test --------------------
model = FinalCNN(dropout_rate=0.1, learning_rate=1e-4)
datamodule = StockDataModule(dataset, batch_size=32)

trainer = pl.Trainer(max_epochs=400, logger=False, enable_progress_bar=True)
trainer.fit(model, datamodule=datamodule)
trainer.test(model, datamodule=datamodule)

# -------------------- Step 7: Save the Model --------------------
os.makedirs("saved_models", exist_ok=True)
torch.save(model.state_dict(), "saved_models/final_cnn_real_mse.pth")
print("✅ Model saved to saved_models/final_cnn_real_mse.pth")

# -------------------- Step 8: Parameter Count --------------------
def count_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

final_param_count = count_parameters(model)
print(f"Total Trainable Parameters: {final_param_count}")


INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
/usr/local/lib/python3.11/dist-packages/pytorch_lightning/callbacks/model_checkpoint.py:654: Checkpoint directory /content/checkpoints exists and is not empty.
INFO:pytorch_lightning.callbacks.model_summary:
   | Name      | Type              | Params | Mode 
---------------------------------------------------------
0  | conv1     | Conv1d            | 3.2 K  | train
1  | bn1       | BatchNorm1d       | 64     | train
2  | conv2     | Conv1d            | 6.2 K  | train
3  | bn2       | BatchNorm1d       | 128    | train
4  | conv3     | Conv1d            | 2.1 K  | train
5  | b

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:610: UserWarning: Using a target size (torch.Size([1])) that is different to the input size (torch.Size([])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


...

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=400` reached.


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│         test_mse          │    32.093292236328125     │
└───────────────────────────┴───────────────────────────┘

✅ Model saved to saved_models/final_cnn_real_mse.pth
Total Trainable Parameters: 12865


<ipython-input-29-aecf48abc8a1>:157: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  return sum(p.numel() for p in model.parameters() if p.requires_grad)
